# LDA Topic Modelling

* This notebook is showcases the process of building an NLP Topic Model using `Latent Dirichlet Allocation` method. 
* The dataset we are going to use are `text` and `soft text` from `scrapped_fox_data_clean.csv`. 

## Table Of Contents

## Installations


In [1]:
# ## installing required libraries
# ! pip install beautifulsoup4
# ! pip install pandas
# ! pip install numpy
# ! pip install plotly
# ! pip install nbformat
# ! pip install ipykernel
# ! pip install matplotlip
# ! pip install wordcloud
# ! pip install gensim
# ! pip install pyLDAvis
# ! pip install nltk
# ! pip install -U pip setuptools wheel
# ! pip install -U spacy
# ! python -m spacy download en_core_web_trf 
# ! python -m spacy download en_core_web_md
# ! pip install joblib
# ! pip install tqdm

## Imports

In [28]:

import pandas as pd
# pd.set_option('display.max_rows', 500)
# pd.set_option('display.max_columns', 500)
# pd.set_option('display.width', 1000)

import re
import string
from bs4 import BeautifulSoup
import nltk
from nltk.stem import PorterStemmer
from nltk.stem.wordnet import WordNetLemmatizer
nltk.download('stopwords')
from pprint import pprint

import spacy
from sklearn.feature_extraction.text import TfidfVectorizer, CountVectorizer
from sklearn.model_selection import train_test_split
from sklearn.decomposition import LatentDirichletAllocation
from sklearn.model_selection import GridSearchCV

from gensim import corpora, models
from gensim.utils import simple_preprocess
from gensim.models import Phrases
from gensim.models.phrases import Phraser
from gensim.models import CoherenceModel
from gensim.models.ldamodel import LdaModel
from gensim.models.ldamulticore import LdaMulticore

# Plotting tools
import pyLDAvis
import pyLDAvis.sklearn
import pyLDAvis.gensim_models as gensimvis
import matplotlib.pyplot as plt
%matplotlib inline

import plotly.express as px
import plotly.graph_objects as go
import plotly.io as io

# loading library
import pickle

from joblib import dump, load

from tqdm.auto import tqdm

import os
import sys
sys.path.insert(0, os.path.abspath('../utils'))

## importing custom modules
import common_utils
import gensim_utils
import sklearn_utils


[nltk_data] Downloading package stopwords to
[nltk_data]     C:\Users\gaura\AppData\Roaming\nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


## Reading Data

In [16]:
## reading manaully scrapped data
data = pd.read_csv('../data/scrapped_fox_data_clean.csv')
print(data.shape)

(3972, 12)


## Utility Functions

### Preparing Stop Words

In [111]:
## extending stopwords
# lets break down the cleaning functions into smaller functions
stop_words = nltk.corpus.stopwords.words('english')

## trying to remove stopwords from stopwords super set. 
stopwords_super_set = pd.read_csv("../data/stopwords/sw1k.csv")

## filtering stopwords to pronouns and other type
stopwords_to_remove = list(stopwords_super_set.loc[(stopwords_super_set["type"] == "G" ), "term"])


# stop_words.extend(['from', 'subject', 're', 'edu', 'use', 'say', 'one', 'time', 'people',
#                   'know', 'like', 'tell', 'get', 'year', 'go', 'around', 'award', 'actually', 'carry',
#                    'new', 'it', 'show', 'news', 'go', 'fox', 'make', 'do', 'not', 'say',
#                    'also', 'love', 'it', 'star', 'go', 'do', 'say', 'not', 'said'
#                    ])

stop_words.extend(stopwords_to_remove)
stop_words.extend(['monday', 'tuesday', 'wednesday', 
                   'thursday', 'friday', 'saturday', 'sunday'])
print(stop_words)

['i', 'me', 'my', 'myself', 'we', 'our', 'ours', 'ourselves', 'you', "you're", "you've", "you'll", "you'd", 'your', 'yours', 'yourself', 'yourselves', 'he', 'him', 'his', 'himself', 'she', "she's", 'her', 'hers', 'herself', 'it', "it's", 'its', 'itself', 'they', 'them', 'their', 'theirs', 'themselves', 'what', 'which', 'who', 'whom', 'this', 'that', "that'll", 'these', 'those', 'am', 'is', 'are', 'was', 'were', 'be', 'been', 'being', 'have', 'has', 'had', 'having', 'do', 'does', 'did', 'doing', 'a', 'an', 'the', 'and', 'but', 'if', 'or', 'because', 'as', 'until', 'while', 'of', 'at', 'by', 'for', 'with', 'about', 'against', 'between', 'into', 'through', 'during', 'before', 'after', 'above', 'below', 'to', 'from', 'up', 'down', 'in', 'out', 'on', 'off', 'over', 'under', 'again', 'further', 'then', 'once', 'here', 'there', 'when', 'where', 'why', 'how', 'all', 'any', 'both', 'each', 'few', 'more', 'most', 'other', 'some', 'such', 'no', 'nor', 'not', 'only', 'own', 'same', 'so', 'than', '

### Common Utility Functions

In [112]:
# nlp = spacy.load('en_core_web_md')
# # nlp = spacy.load('en_core_web_trf')
# nlp.add_pipe('merge_entities')
# # nlp.add_pipe("merge_noun_chunks")
# tqdm.pandas(desc="processing")

# # Utility Functions for Text Cleaning
# def sent_to_words(sentences):
#     for sentence in tqdm(sentences):
#         yield (simple_preprocess(str(sentence), deacc=True))

# # function to clean html tags from text


# def clean_html(html):
#     # parse html content
#     soup = BeautifulSoup(html, "html.parser")
#     for data in soup(['style', 'script', 'code', 'a']):
#         # Remove tags
#         data.decompose()
#     # return data by retrieving the tag content
#     return ' '.join(soup.stripped_strings)

# # function to convert text to lowercase


# def lower_case(text):
#     return text.lower()

# # function to remove line breaks


# def remove_line_breaks(text):
#     return re.sub(r'\n', '', text)

# # function to remove punctuation


# def remove_punctuation(text):
#     return text.translate(str.maketrans('', '', string.punctuation))

# # function to remove numbers


# def remove_numbers(text):
#     return re.sub(r'\d+', '', text)

# # function to remove extra spaces


# def remove_extra_spaces(text):
#     text = text.replace(u'\xa0', u' ')
#     return text
#     # return re.sub(' +', ' ', text)

# # function to remove stopwords


# def remove_stopwords(texts):
#     preprocess_text = simple_preprocess(str(texts), deacc=True)
#     word_list = [word for word in preprocess_text if word not in stop_words]
#     return " ".join(word_list)
#     # return [[word for word in simple_preprocess(str(doc)) if word not in stop_words] for doc in texts]

# # helper function to create pos tags


# def create_pos_tag(str_sent):
#     return nlp(str_sent)

# # function for text lemmatization using spac
# ##'ADJ', 'VERB'
# def lemmatization(texts, allowed_postags=['PROPN', 'NOUN']):
#     """https://spacy.io/api/annotation"""
#     texts_out = []
#     for sent in tqdm(texts):
#         doc = nlp(" ".join(sent))
#         texts_out.append(
#             [token.lemma_ for token in doc if (token.pos_ in allowed_postags and token.is_stop == False and token.text not in stop_words)])
#     return texts_out


# def tokenization(texts, allowed_postags=['PROPN', 'NOUN']):
#     """https://spacy.io/api/annotation"""
#     texts_out = []
#     for sent in tqdm(texts):
#         doc = nlp(" ".join(sent))
#         texts_out.append(
#             ["_".join(token.text.split(" ")) for token in doc if (token.pos_ in allowed_postags and token.is_stop == False and token.text not in stop_words)])
#     return texts_out

# def lemmatization_without_pos(texts):
#     """https://spacy.io/api/annotation"""
#     texts_out = []
#     for sent in texts:
#         doc = nlp(" ".join(sent))
#         texts_out.append(
#             [token.lemma_ for token in doc])
#     return texts_out


# def make_bigrams(texts, bigram_mod):
#     return [bigram_mod[doc] for doc in texts]


# def make_trigrams(texts, bigram_mod, trigram_mod):
#     return [trigram_mod[bigram_mod[doc]] for doc in texts]

# ## helper function to create pos tags distribution
# def create_pos_tags_distribution(docs = []):
#     token_distribution = {}
#     is_alpha = 0
#     is_stop = 0
#     for doc in tqdm(docs):
#         for token in doc:
#             token_distribution[token.pos_] = token_distribution.get(token.pos_, 0) + 1
#             if(token.is_alpha):
#                 is_alpha += 1
#             if(token.is_stop):
#                 is_stop += 1
#     return token_distribution, is_alpha, is_stop


# # function to create n-grams from noun chunks
# def create_noun_chunk_ngrams(docs):
#     n_gram_docs = []
#     for doc in docs:
#         doc_text = doc.text
#         for chunk in doc.noun_chunks:
#             chunk_n_gram = "_".join(chunk.text.split(" "))
#             doc_text = doc_text.replace(chunk.text, chunk_n_gram)
#         n_gram_docs.append(doc_text.split(" "))
#     return n_gram_docs


# def lemmatization_noun_chunks(texts):
#     """https://spacy.io/api/annotation"""
#     texts_out = []
#     for sent in texts:
#         doc = nlp(" ".join(sent))
#         texts_out.append([token.lemma_ for token in doc if (
#             ("_" in token.text) or ## if the token is a noun chunk allow that
#             (token.pos_ in ['NOUN', 'PROPN'] and token.is_alpha and token.is_stop == False) ## if the token is a noun or proper noun allow that
#         )])
#     return texts_out

### Gensim Models Utility Functions

In [203]:
# ## function to compute optimal parameters for LDA model
# def compute_coherence_values(corpus, id2word, texts, num_topics, passes, chunk_sizes=[200], iterations=[100]):
#     """
#     Compute c_v coherence for various number of topics

#     Parameters:
#     ----------
#     dictionary : Gensim dictionary
#     corpus : Gensim corpus
#     texts : List of input texts
#     limit : Max num of topics

#     Returns:
#     -------
#     model_list : List of LDA topic models
#     coherence_values : Coherence values corresponding to the LDA model with respective number of topics
#     """
#     coherence_values = []
#     model_list = []
#     params = []
#     for num_topic in tqdm(num_topics):
#         # for chunk_size in tqdm(chunk_sizes):
#             for num_passes in tqdm(passes):
#                 for iteration in tqdm(iterations):
#                     model = LdaModel(corpus=corpus,
#                                     id2word=id2word,
#                                     num_topics=num_topic,
#                                     random_state=100,
#                                     update_every=1,
#                                     # chunksize=chunk_size,
#                                     passes=num_passes,
#                                     iterations=iteration,
#                                     per_word_topics=True)
#                     model_list.append(model)
#                     # Compute Perplexity
#                     perplexity = model.log_perplexity(corpus)
                    
#                     # Compute Coherence Score
#                     coherence_model_lda = CoherenceModel(model=model, texts=texts, dictionary=id2word, coherence='c_v')
#                     cv_coherence = coherence_model_lda.get_coherence()
                    
#                     coherence_model_umass = CoherenceModel(model=model, texts=texts, dictionary=id2word, coherence='u_mass')
#                     umass_coherence = coherence_model_umass.get_coherence()
                                    
#                     coherence_values.append({
#                         "perplexity": perplexity,
#                         "cv_coherence": cv_coherence,
#                         "umass_coherence": umass_coherence,
#                     })
#                     params.append({'num_topics': num_topic, 'chunk_size': "chunk_size", 'passes': num_passes, 'iterations': iteration})

#     return model_list, coherence_values, params

# def analyze_gensim_lda_model(lda_model, corpus, id2word, texts, num_topics, passes, chunk_sizes=[200]):
#     # Compute Perplexity
#     print('\nPerplexity: ', lda_model.log_perplexity(corpus))  # a measure of how good the model is. lower the better.
#     # Compute Coherence Score
#     coherence_model_lda = CoherenceModel(model=lda_model, texts=texts, dictionary=id2word, coherence='c_v')
#     coherence_lda = coherence_model_lda.get_coherence()
#     print('\nCoherence Score: ', coherence_lda)

# ## helper functions to visualize LDA model
# def visualize_gensim_lda_model(lda_model, corpus, id2word, filename="gensim_lda.html"):
#     # Visualize the topics
#     pyLDAvis.enable_notebook()
#     vis = gensimvis.prepare(lda_model, corpus, id2word)
#     vis.save(filename)

### Sklearn Model Utility Functions

In [114]:
# import numpy as np


# # Styling
# def color_green(val):
#     color = 'green' if val > .1 else 'black'
#     return 'color: {col}'.format(col=color)

# def make_bold(val):
#     weight = 700 if val > .1 else 400
#     return 'font-weight: {weight}'.format(weight=weight)


# def print_sklearn_sparcity(data_vectorized):
#     # Materialize the sparse data
#     data_dense = data_vectorized.todense()

#     # Compute Sparsicity = Percentage of Non-Zero cells
#     print("Sparsicity: ", ((data_dense > 0).sum()/data_dense.size)*100, "%")


# def create_sklearn_dominent_topic_dataframe(lda_model, data_vectorized):
#     lda_output = lda_model.transform(data_vectorized)
#     # column names
#     topicnames = ["Topic" + str(i) for i in range(lda_model.n_components)]
#     # index names
#     docnames = ["Doc" + str(i) for i in range(len(data))]
    
#     df_document_topic = pd.DataFrame(np.round(lda_output, 2), columns=topicnames, index=docnames)
#     # Get dominant topic for each document
#     dominant_topic = np.argmax(df_document_topic.values, axis=1)
#     df_document_topic['dominant_topic'] = dominant_topic
#     return df_document_topic

# def print_sklearn_dominant_topics(lda_model, data_vectorized):
#     df_document_topic = create_sklearn_dominent_topic_dataframe(lda_model, data_vectorized)
#     # Apply Style
#     df_document_topics = df_document_topic.head(15).style.applymap(color_green).applymap(make_bold)
#     return df_document_topics

# def print_sklearn_topic_distribution(lda_model, data_vectorized):
#     df_document_topic = create_sklearn_dominent_topic_dataframe(lda_model, data_vectorized)
#     df_topic_distribution = df_document_topic['dominant_topic'].value_counts().reset_index(name="Num Documents").rename(columns={'index':'Topic'})
#     # df_topic_distribution.columns = ["Topic Num", "Num Documents"]
#     return df_topic_distribution


# # Show top n keywords for each topic
# def show_sklearn_topics(vectorizer, lda_model, n_words=20):
#     keywords = np.array(vectorizer.get_feature_names_out())
#     topic_keywords = []
#     for topic_weights in lda_model.components_:
#         top_keyword_locs = (-topic_weights).argsort()[:n_words]
#         topic_keywords.append(keywords.take(top_keyword_locs))
#     return topic_keywords

# def format_sklearn_topics(topic_keywords):
#     df_topic_keywords = pd.DataFrame(topic_keywords)
#     df_topic_keywords.columns = ['Word '+str(i) for i in range(df_topic_keywords.shape[1])]
#     df_topic_keywords.index = ['Topic '+str(i) for i in range(df_topic_keywords.shape[0])]
#     return df_topic_keywords

# def analyze_sklearn_lda_model(lda_model, data_vectorized):
#     # Log Likelyhood: Higher the better
#     print("Log Likelihood: ", lda_model.score(data_vectorized))
#     # Perplexity: Lower the better. Perplexity = exp(-1. * log-likelihood per word)
#     print("Perplexity: ", lda_model.perplexity(data_vectorized))

# ## helper function to visualize lda model
# def visualize_sklearn_lda_model(lda_model, data_vectorized, vectorizer, mds='tsne'):    
#     pyLDAvis.enable_notebook()
#     panel2 = pyLDAvis.sklearn.prepare(lda_model, data_vectorized, vectorizer, mds=mds)
#     return panel2

## Text Pre-processing

In [18]:
def preprocess_text(text):
     text = common_utils.clean_html(text)
     text = common_utils.lower_case(text)
     text = common_utils.remove_line_breaks(text)
     text = common_utils.remove_punctuation(text)
     text = common_utils.remove_numbers(text)
     text = common_utils.remove_extra_spaces(text)
     # text = remove_stopwords(text)
     return text

data["clean_text"] = data["text"].progress_apply(preprocess_text)

processing: 100%|██████████| 3972/3972 [00:01<00:00, 2367.07it/s]


### Tokenizing

In [116]:
data_words = list(common_utils.sent_to_words(data['clean_text']))

100%|██████████| 3972/3972 [00:04<00:00, 899.81it/s]


## EDA on text Data

In [117]:
## check for duplicates
data["clean_text"].duplicated().sum()

0

In [118]:
data['text_word_count'] = data['clean_text'].progress_apply(lambda x: len(str(x).split(" ")))

data['text_word_count'].describe()


processing: 100%|██████████| 3972/3972 [00:00<00:00, 31052.12it/s]


count    3972.000000
mean      615.245972
std       342.681649
min        29.000000
25%       402.000000
50%       538.000000
75%       738.000000
max      9672.000000
Name: text_word_count, dtype: float64

In [119]:
## checking the distribution of word count in text
fig = px.histogram(data, x="text_word_count", title="Distribution of Word Count in text")
fig.show()

d:\workspace\Aletheia\env\lib\site-packages\plotly\io\_renderers.py:395: DeprecationWarning:

distutils Version classes are deprecated. Use packaging.version instead.

d:\workspace\Aletheia\env\lib\site-packages\plotly\io\_renderers.py:395: DeprecationWarning:

distutils Version classes are deprecated. Use packaging.version instead.



##### Notes
* Word counts are fairly distributed. 

In [120]:
from joblib import Parallel, delayed

def chunker(iterable, total_length, chunksize):
    return (iterable[pos: pos + chunksize] for pos in range(0, total_length, chunksize))

def flatten(list_of_lists):
    print("flatten a list of lists to a combined list")
    return [item for sublist in list_of_lists for item in sublist]

def process_chunk(texts):
    nlp_list = list(nlp.pipe(texts, batch_size=100, n_process=100))
    print("processing chunk..")
    return nlp_list

def preprocess_parallel(texts, chunksize=1000):
    executor = Parallel(n_jobs=50, backend='multiprocessing', prefer="processes")
    do = delayed(process_chunk)
    tasks = (do(chunk) for chunk in chunker(texts, len(data), chunksize=chunksize))
    print("Processing {} texts in {} jobs".format(len(data), 50))
    result = executor(tasks)
    return flatten(result)

In [121]:
clean_text_list = list(data['clean_text'])
len(clean_text_list)

3972

In [122]:
## lets create POS tags for each text and see the distribution of POS tags
docs = [nlp(text) for text in tqdm(data['clean_text'])]


100%|██████████| 3972/3972 [04:02<00:00, 16.40it/s]


In [123]:
## creating pos tags distribution
token_distribution, is_alpha, is_stop = common_utils.create_pos_tags_distribution(docs)

100%|██████████| 3972/3972 [00:01<00:00, 3799.23it/s]


In [124]:
## convert the dictionary to a dataframe
token_distribution_df = pd.DataFrame.from_dict(token_distribution, orient='index', columns=['count']).reset_index().rename(columns={"index": "tags"})


In [125]:
## lets create a distribution of POS tags
## checking the distribution of word count in text
fig = px.histogram(token_distribution_df, x="tags", y="count", title="Distribution POS Tags in text")
fig.show()

d:\workspace\Aletheia\env\lib\site-packages\plotly\io\_renderers.py:395: DeprecationWarning:

distutils Version classes are deprecated. Use packaging.version instead.

d:\workspace\Aletheia\env\lib\site-packages\plotly\io\_renderers.py:395: DeprecationWarning:

distutils Version classes are deprecated. Use packaging.version instead.



In [126]:
## lets see how many words are alpha and how many are stop words
print(f"we have total {data['text_word_count'].sum()} words in the text. Out of which {is_alpha} are alpha and {is_stop} are stop words")

##we have total 2384515 words in the text. Out of which 1275765 are alpha and 780851 are stop words


we have total 2443757 words in the text. Out of which 2210843 are alpha and 1065545 are stop words


##### Notes
* It seems we still have some numerical and non-alpha values even after cleaning it. Lets check them out so make sure if it needs more cleaning


In [127]:
for doc in docs:
    for token in doc:
        if(token.is_alpha == False):
            print(token.text, token.pos_, token.is_stop,len(token.text.split(" ")))

maggie hassan PROPN False 2
new hampshire PROPN False 2
don bolduc PROPN False 2
’s VERB True 1
– PUNCT False 1
– PUNCT False 1
saint anselm college’s PROPN False 3
new hampshire PROPN False 2
wednesday evening NOUN False 2
  SPACE False 2
rick wiley PROPN False 2
fox news NOUN False 2
  SPACE False 2
kevin donohoe PROPN False 2
nancy pelosi PROPN False 2
’s PART True 1
san francisco PROPN False 2
kate constantini PROPN False 2
fox news NOUN False 2
’s VERB True 1
’s AUX True 1
new hampshire PROPN False 2
midseptember bolduc PROPN False 2
chuck morse NOUN False 2
gop gov PROPN False 2
chris sununu PROPN False 2
the past six weeks NOUN False 4
’s PART True 1
’s VERB True 1
six days NOUN False 2
  SPACE False 2
’s PART True 1
last year NOUN False 2
the supreme court’s PROPN False 3
fox news NOUN False 2
earlier this month NOUN False 3
sen lindsey graham PROPN False 3
south carolina PROPN False 2
’s PART True 1
’s PART True 1
  SPACE False 2
’s AUX True 1
’s AUX True 1
’s PART True 1
n’t 

##### Notes
* Interesting, `Spacy` is tagging `noun` and `entity` chunks as `non alpha` tokens.  That could be an issue. We'll have to make sure lemmatization function can handle this. 

##### Notes
* So `maximum` tags are
    * `NOUN` - noun
    * `VERB` - verb    
    * `ADP` - adposition    
    * `PROPN`- proper noun
    * `PUNCT` - punctuation
    * `ADJ` - adjective
* Since these are news article texts, I think useful tags are, 
    * `PROPN`
    * `NOUN`
    * `ADJ` - Not sure about adjective yet. 
    * `VERB` - Not sure about verb yet. 
* We can remove rest of the words and still have a decent topic model. 
* We can also use the `is_stop` and `is_alpha` tags to remove the stopwords and non alpha tokens.
    * Lets update the helper functions accordingly. 

### Word Frequency

In [91]:
from collections import Counter
# lets see if we can calculate word frequency
# all tokens that arent stop words or punctuations
words = []
for doc in tqdm(docs):
    doc_words = [token.text for token in doc if token.pos_ in ['PROPN', 'NOUN'] and not token.is_stop and not token.is_punct and token.is_alpha]
    words.append(doc_words)

flat_list = [item for sublist in words for item in sublist]


word_counts = Counter(flat_list)
word_counts.most_common(10)


100%|██████████| 3972/3972 [00:00<00:00, 4774.75it/s]


[('news', 11478),
 ('fox', 11456),
 ('biden', 8447),
 ('president', 7925),
 ('house', 6630),
 ('trump', 5970),
 ('state', 5862),
 ('democrats', 5299),
 ('senate', 4572),
 ('republicans', 4512)]

In [92]:
## lets try and plot the word cloud
word_counts_df = pd.DataFrame.from_dict(word_counts, orient='index', columns=['count']).reset_index().rename(columns={"index": "word"})

fig = px.histogram(word_counts_df, x="word", y="count", title="Distribution POS Tags in text")
fig.show()

d:\workspace\Aletheia\env\lib\site-packages\plotly\io\_renderers.py:395: DeprecationWarning:

distutils Version classes are deprecated. Use packaging.version instead.

d:\workspace\Aletheia\env\lib\site-packages\plotly\io\_renderers.py:395: DeprecationWarning:

distutils Version classes are deprecated. Use packaging.version instead.



In [93]:
word_counts_df.describe()

count
count  24086.000000
mean      34.059827
std      216.496122
min        1.000000
25%        1.000000
50%        3.000000
75%       11.000000
max    11478.000000

##### Notes
* Interesting the difference between `mean` and `max` frequency is quick big.  Wonder if that would cause issues in the model. 
* May be IF-IDF might be a good candidate to balance out the frequency difference

In [94]:
## lets look at spacy merge entities 
# nlp.add_pipe("merge_noun_chunks")
merged_docs = [nlp(text) for text in tqdm(data['clean_text'])]


100%|██████████| 3972/3972 [03:49<00:00, 17.29it/s]


## Creating Bigram & Tigram Models

In [128]:
# Build the bigram and trigram models
bigram = Phrases(data_words, min_count=5, threshold=100) # higher threshold fewer phrases.
trigram = Phrases(bigram[data_words], threshold=100)  

# Faster way to get a sentence clubbed as a trigram/bigram
bigram_mod = Phraser(bigram)
trigram_mod = Phraser(trigram)

## Gensim LDA with BOW

### Lemmatization

In [165]:
# Do lemmatization
data_lemmatized = common_utils.tokenization(data_words)

print(data_lemmatized[:1])

100%|██████████| 3972/3972 [03:50<00:00, 17.27it/s]

[['governor', 'term', 'democratic', 'sen', 'maggie_hassan', 'new_hampshire', 'republican', 'challenger', 'don_bolduc', 'aim', 'inflation', 'abortion', 'border', 'crisis', 'denialism', 'debate', 'battleground', 'race', 'handful', 'gop', 'senate', 'majority', 'crossfire', 'debate', 'army', 'tours', 'duty', 'war', 'afghanistan', 'debate', 'saint_anselm_college_new_hampshire_institute_of_politics', 'wednesday_evening', 'bolduc', 'campaign', 'bystander', 'crowd', 'debate', 'swing', 'campaign', 'bolduc', 'rick_wiley', 'bolduc', 'campaign', 'fox_news', 'punch', 'activist', 'countdown', 'stake', 'midterm', 'elections', 'campaign', 'communications', 'kevin_donohoe', 'incident', 'behavior', 'activist', 'campaign', 'volunteers', 'debate', 'bolduc', 'altercation', 'debate', 'hassan', 'attack', 'speaker', 'nancy_pelosi', 'husband', 'san_francisco', 'gop', 'senate', 'nominee', 'problems', 'republicans', 'democrat', 'fuel', 'individual', 'bolduc', 'campaign', 'spokesperson', 'kate_constantini', 'fox_

### Create Dictionary & Corpus

In [168]:
# Create Dictionary
id2word = corpora.Dictionary(data_lemmatized)
## filter out words that occur less than 10 documents, or more than 75% of the documents.
id2word.filter_extremes(no_below=10, no_above=0.75, keep_n=10000)
# Create Corpus
texts = data_lemmatized

# Term Document Frequency
corpus = [id2word.doc2bow(text) for text in texts]

# View
print(corpus[:1])

[[(0, 8), (1, 2), (2, 1), (3, 1), (4, 2), (5, 1), (6, 1), (7, 1), (8, 2), (9, 2), (10, 1), (11, 1), (12, 1), (13, 1), (14, 1), (15, 13), (16, 1), (17, 10), (18, 1), (19, 1), (20, 2), (21, 1), (22, 1), (23, 1), (24, 1), (25, 1), (26, 1), (27, 1), (28, 1), (29, 1), (30, 1), (31, 1), (32, 2), (33, 1), (34, 11), (35, 2), (36, 1), (37, 1), (38, 1), (39, 1), (40, 1), (41, 5), (42, 1), (43, 1), (44, 1), (45, 1), (46, 1), (47, 1), (48, 2), (49, 1), (50, 1), (51, 1), (52, 1), (53, 1), (54, 1), (55, 4), (56, 2), (57, 1), (58, 1), (59, 1), (60, 2), (61, 6), (62, 1), (63, 5), (64, 1), (65, 1), (66, 1), (67, 8), (68, 1), (69, 1), (70, 1), (71, 1), (72, 2), (73, 3), (74, 1), (75, 1), (76, 1), (77, 1), (78, 2), (79, 2), (80, 1), (81, 1), (82, 2), (83, 1), (84, 1), (85, 1), (86, 1), (87, 1), (88, 1), (89, 1), (90, 5), (91, 4), (92, 3), (93, 3), (94, 1), (95, 2), (96, 1), (97, 1), (98, 1), (99, 1), (100, 1), (101, 1), (102, 3), (103, 2), (104, 2), (105, 1), (106, 1), (107, 2), (108, 1), (109, 1), (110,

In [169]:
# Human readable format of corpus (term-frequency)
[[(id2word[id], freq) for id, freq in cp] for cp in corpus[:1]]

[[('abortion', 8),
  ('activist', 2),
  ('afghanistan', 1),
  ('aim', 1),
  ('army', 2),
  ('attack', 1),
  ('attacks', 1),
  ('ballot', 1),
  ('ban', 2),
  ('battleground', 2),
  ('behavior', 1),
  ('bid', 1),
  ('biden', 1),
  ('biden_administration', 1),
  ('bills', 1),
  ('bolduc', 13),
  ('border', 1),
  ('campaign', 10),
  ('candidates', 1),
  ('care', 1),
  ('challenger', 2),
  ('chance', 1),
  ('chris_sununu', 1),
  ('chuck_morse', 1),
  ('click', 1),
  ('clips', 1),
  ('communications', 1),
  ('conclusion', 1),
  ('contest', 1),
  ('countdown', 1),
  ('credentials', 1),
  ('crisis', 1),
  ('crowd', 2),
  ('cycle', 1),
  ('debate', 11),
  ('decisions', 2),
  ('democrat', 1),
  ('democratic', 1),
  ('digit', 1),
  ('discourse', 1),
  ('doctor', 1),
  ('don_bolduc', 5),
  ('donald_trump', 1),
  ('doubt', 1),
  ('drug', 1),
  ('duty', 1),
  ('earlier_this_month', 1),
  ('efforts', 1),
  ('elections', 2),
  ('endorsement', 1),
  ('enforcement', 1),
  ('error', 1),
  ('extremism', 1

### Building the Topic Model

In [180]:
lda_model = LdaModel(corpus=corpus,
                     id2word=id2word,
                     num_topics=15,
                     random_state=100,
                     update_every=1,
                    #  chunksize=200,
                     passes=250,
                     iterations=120,
                     alpha='auto',
                     per_word_topics=True)

In [182]:
# Print the Keyword in the 10 topics
pprint(lda_model.print_topics())
# doc_lda = lda_model[corpus]

[(0,
  '0.031*"china" + 0.028*"biden" + 0.018*"taiwan" + 0.017*"ukraine" + '
  '0.016*"administration" + 0.015*"president" + 0.015*"russia" + '
  '0.013*"the_united_states" + 0.013*"afghanistan" + 0.010*"war"'),
 (1,
  '0.049*"police" + 0.023*"crime" + 0.019*"enforcement" + 0.013*"violence" + '
  '0.012*"campaign" + 0.012*"officers" + 0.010*"attorney" + 0.009*"bail" + '
  '0.007*"justice" + 0.007*"charges"'),
 (2,
  '0.031*"justice" + 0.019*"supreme_court" + 0.018*"justices" + '
  '0.016*"lawsuit" + 0.015*"the_supreme_court" + 0.012*"judge" + '
  '0.011*"amendment" + 0.010*"courts" + 0.010*"opinion" + 0.009*"district"'),
 (3,
  '0.045*"iran" + 0.026*"israel" + 0.020*"queen" + 0.014*"north_carolina" + '
  '0.013*"johnson" + 0.013*"biden" + 0.013*"president" + 0.011*"regime" + '
  '0.010*"senators" + 0.009*"king"'),
 (4,
  '0.072*"voters" + 0.051*"democrats" + 0.036*"poll" + 0.028*"elections" + '
  '0.027*"republicans" + 0.026*"midterm" + 0.018*"inflation" + 0.017*"georgia" '
  '+ 0.016*

### Analyzing Model

In [183]:
# Compute Perplexity
print('\nPerplexity: ', lda_model.log_perplexity(corpus))  # a measure of how good the model is. lower the better.

# Compute Coherence Score
coherence_model_lda = CoherenceModel(model=lda_model, texts=data_lemmatized, dictionary=id2word, coherence='c_v')
coherence_lda = coherence_model_lda.get_coherence()
print('\nCV Coherence Score: ', coherence_lda)

coherence_model_umass = CoherenceModel(model=lda_model, texts=data_lemmatized, dictionary=id2word, coherence='u_mass')
coherence_lda = coherence_model_umass.get_coherence()
print('\nuMass Coherence Score: ', coherence_lda)


Perplexity:  -6.929646047519937

CV Coherence Score:  0.5554490793630982

uMass Coherence Score:  -2.4774150787821116


##### Notes to Delete

###### Manual Grid Search
-------------------------------------------------

```
Worth Saving
lda_model = LdaModel(corpus=corpus,
                     id2word=id2word,
                     num_topics=30,
                     random_state=100,
                     update_every=1,
                     passes=250,
                     alpha='auto',
                     per_word_topics=True)

Perplexity:  -5.722810366840693
Coherence Score:  0.4411146751458711
```

---------------------------------------------------------
```
lda_model = LdaModel(corpus=corpus,
                     id2word=id2word,
                     num_topics=25,
                     random_state=100,
                     update_every=1,
                    #  chunksize=200,
                     passes=250,
                     alpha='auto',
                     per_word_topics=True)


Perplexity:  -5.715112582723044
Coherence Score:  0.4510137020042296
```
---------------------------------------------------------------

```
lda_model = LdaModel(corpus=corpus,
                     id2word=id2word,
                     num_topics=15,
                     random_state=100,
                     update_every=1,
                    #  chunksize=200,
                     passes=250,
                     alpha='auto',
                     per_word_topics=True)


Perplexity:  -5.73645354360661
Coherence Score:  0.4648348586102282                     
```
----------------------------------------------------------------------
```
Works with token.lemma_ and not token.text
lda_model = LdaModel(corpus=corpus,
                     id2word=id2word,
                     num_topics=15,
                     random_state=100,
                     update_every=1,
                    #  chunksize=200,
                     passes=250,
                     alpha='auto',
                     per_word_topics=True)


Perplexity:  -6.204518508321434
Coherence Score:  0.47021907190499096
```
-----------------------------------------------------------------------------
##### Tokenized Data without `noun chunks` and `named entity chunks`
```
lda_model = LdaModel(corpus=corpus,
                     id2word=id2word,
                     num_topics=15,
                     random_state=100,
                     update_every=1,
                    #  chunksize=200,
                     passes=250,
                     alpha='auto',
                     per_word_topics=True)



Perplexity:  -6.875836169151711
Coherence Score:  0.5762156296311478
```
------------------------------------------------------------------------------
##### Tokenized data with noun and entitiy chunks

```
lda_model = LdaModel(corpus=corpus,
                     id2word=id2word,
                     num_topics=15,
                     random_state=100,
                     update_every=1,
                    #  chunksize=200,
                     passes=250,
                     alpha='auto',
                     per_word_topics=True)

Perplexity:  -7.3730853354515915
Coherence Score:  0.5226321487478642
```
----------------------------------------------------------------------------------
##### Tokenized with just named_entity chunks

```
lda_model = LdaModel(corpus=corpus,
                     id2word=id2word,
                     num_topics=15,
                     random_state=100,
                     update_every=1,
                    #  chunksize=200,
                     passes=250,
                     alpha='auto',
                     per_word_topics=True)


Perplexity:  -6.91509928727058
Coherence Score:  0.5916526920931731
```


-----------------------------------------------------------------------------------
##### Tokenized with just named_entity chunks

```
lda_model = LdaModel(corpus=corpus,
                     id2word=id2word,
                     num_topics=15,
                     random_state=100,
                     update_every=1,
                    #  chunksize=200,
                     passes=250,
                     iterations=100,
                     alpha='auto',
                     per_word_topics=True)


Perplexity:  -6.923146151007259
CV Coherence Score:  0.602559024821954
uMass Coherence Score:  -2.101086011129721
```

### Visualize Topics

In [184]:
# Visualize the topics
pyLDAvis.enable_notebook()
vis = gensimvis.prepare(lda_model, corpus, id2word)
vis

d:\workspace\Aletheia\env\lib\site-packages\pyLDAvis\_prepare.py:247: FutureWarning:

In a future version of pandas all arguments of DataFrame.drop except for the argument 'labels' will be keyword-only.



PreparedData(topic_coordinates=              x         y  topics  cluster       Freq
topic                                                
6      0.240084 -0.030381       1        1  11.918841
8      0.054197 -0.143145       2        1  11.912876
12     0.116894  0.030187       3        1   8.081324
10     0.180113  0.008327       4        1   7.245185
9     -0.125608 -0.033552       5        1   6.943067
1     -0.121867  0.033022       6        1   6.938647
4      0.298287  0.007333       7        1   6.647584
7     -0.052299 -0.031052       8        1   6.629645
13    -0.140872  0.049185       9        1   6.444941
11    -0.143665 -0.028712      10        1   6.442271
0     -0.135716 -0.141805      11        1   6.103107
2     -0.130903  0.223352      12        1   4.532179
5      0.014494  0.275955      13        1   4.531695
14     0.033248 -0.034066      14        1   3.720826
3     -0.086388 -0.184647      15        1   1.907812, topic_info=                  Term         Freq        Total Category  logprob  loglift
0             abortion  3335.000000  3335.000000  Default  30.0000  30.0000
16              border  3281.000000  3281.000000  Default  29.0000  29.0000
138              trump  4465.000000  4465.000000  Default  28.0000  28.0000
203             voters  2916.000000  2916.000000  Default  27.0000  27.0000
162          democrats  5244.000000  5244.000000  Default  26.0000  26.0000
..                 ...          ...          ...      ...      ...      ...
501  the_united_states    78.518725   793.474878  Topic15  -4.8051   1.6461
12               biden   123.963437  5994.858713  Topic15  -4.3484   0.0805
102          president   121.346931  7890.488752  Topic15  -4.3698  -0.2155
154             bidens    56.636768  1020.009714  Topic15  -5.1318   1.0683
119             senate    58.653869  4096.647984  Topic15  -5.0968  -0.2871

[999 rows x 6 columns], token_table=      Topic      Freq      Term
term                           
3100      8  0.998570    abbott
4762     13  0.961052   abbotts
0         1  0.011392  abortion
0         7  0.130703  abortion
0        13  0.857963  abortion
...     ...       ...       ...
1756      2  0.030385     youth
1756      9  0.941948     youth
1756     14  0.020257     youth
1731     11  0.972010      yuma
1757      4  0.993156    zeldin

[2556 rows x 3 columns], R=30, lambda_step=0.01, plot_opts={'xlab': 'PC1', 'ylab': 'PC2'}, topic_order=[7, 9, 13, 11, 10, 2, 5, 8, 14, 12, 1, 3, 6, 15, 4])

lda_model = LdaModel(corpus=corpus,
                     id2word=id2word,
                     num_topics=15,
                     random_state=100,
                     update_every=1,
                    #  chunksize=200,
                     passes=250,
                     iterations=120,
                     alpha='auto',
                     per_word_topics=True)

### Finding Best Parms



In [190]:
## compute_coherence_values(corpus, id2word, texts, num_topics, passes, chunk_sizes=[200], iterations=[100]):
model_list, coherence_values, params = gensim_utils.compute_coherence_values(corpus=corpus, id2word=id2word, texts=data_lemmatized, num_topics=[10, 15, 20, 25], passes=[200, 250, 300], iterations=[100, 120, 150])


  0%|          | 0/4 [00:00<?, ?it/s]



100%|██████████| 3/3 [23:50<00:00, 476.92s/it]




100%|██████████| 3/3 [29:18<00:00, 586.18s/it]




 25%|██▌       | 1/4 [1:27:49<4:23:27, 5269.26s/it]



100%|██████████| 3/3 [23:15<00:00, 465.24s/it]




100%|██████████| 3/3 [28:31<00:00, 570.39s/it]




 50%|█████     | 2/4 [2:53:23<2:52:59, 5189.98s/it]



100%|██████████| 3/3 [23:55<00:00, 478.62s/it]




100%|██████████| 3/3 [29:34<00:00, 591.46s/it]




 75%|███████▌  | 3/4 [4:21:23<1:27:11, 5231.15s/it]



100%|██████████| 3/3 [23:46<00:00, 475.61s/it]




100%|██████████| 3/3 [29:25<00:00, 588.34s/it]




100%|██████████| 4/4 [5:50:43<00:00, 5260.98s/it]  


In [193]:
## lets write to pickle file for future use
# for models in model_list:
#     with open(f"../pickles/text_models/gensim_bow/{models.num_topics}_topics_{models.passes}_passes_{models.iterations}_iterations.pkl", "wb") as f:
#         pickle.dump(models, f)

In [202]:
## les convert the coherence_values list to a dataframe
# coherence_values_df = pd.DataFrame(coherence_values, columns=['perplexity', 'cv_coherence', 'umass_coherence'])


# params_df = pd.DataFrame(params, columns=['num_topics', 'passes'])


# combined_df = pd.concat([params_df, coherence_values_df], axis=1)
# combined_df

# combined_df.to_csv('../pickles/text_models/gensim_bow/combined_df.csv', index=False)

num_topics  passes  perplexity  cv_coherence  umass_coherence
0           10     200   -6.998504      0.530079        -1.928838
1           10     200   -7.003896      0.527507        -1.899064
2           10     200   -7.009518      0.522806        -1.941300
3           10     250   -6.998219      0.527192        -1.926723
4           10     250   -7.003660      0.527507        -1.899524
5           10     250   -7.009314      0.521979        -1.939337
6           10     300   -6.998064      0.527192        -1.925657
7           10     300   -7.003501      0.527507        -1.899750
8           10     300   -7.009193      0.521979        -1.939096
9           15     200   -6.927175      0.598702        -2.078357
10          15     200   -6.933657      0.550770        -2.347129
11          15     200   -6.937755      0.552097        -2.337840
12          15     250   -6.926745      0.601829        -2.033160
13          15     250   -6.933287      0.550770        -2.348002
14          15     250   -6.937144      0.547959        -2.323458
15          15     300   -6.926489      0.602920        -2.027883
16          15     300   -6.933044      0.550840        -2.346599
17          15     300   -6.936722      0.551394        -2.332016
18          20     200   -6.901848      0.563084        -2.608615
19          20     200   -6.906064      0.565873        -2.440997
20          20     200   -6.911796      0.566614        -2.494248
21          20     250   -6.901616      0.562748        -2.605916
22          20     250   -6.905698      0.565802        -2.478855
23          20     250   -6.911473      0.566744        -2.501407
24          20     300   -6.901448      0.562748        -2.605488
25          20     300   -6.905514      0.568321        -2.495676
26          20     300   -6.911339      0.566014        -2.502504
27          25     200   -6.876040      0.584290        -2.197082
28          25     200   -6.881162      0.586874        -2.256091
29          25     200   -6.884038      0.578831        -2.203432
30          25     250   -6.875610      0.584230        -2.193264
31          25     250   -6.880527      0.585364        -2.261674
32          25     250   -6.883790      0.578831        -2.202731
33          25     300   -6.875310      0.583049        -2.195336
34          25     300   -6.880278      0.585579        -2.259617
35          25     300   -6.883603      0.578043        -2.203229

### Write to Pickle File

In [269]:
# create an iterator object with write permission - model.pkl
## just commenting to make sure we don't overwrite the file

# path = "../pickles/text_models/gensim_bow"

# # with open(path + '/features_v1', 'wb') as files:
# #     pickle.dump(features, files)
    
# with open(path + '/model_v1', 'wb') as files:
#     pickle.dump(lda_model, files)    

### Analyzing Best Params

In [9]:
coherence_bow_df = pd.read_csv('../pickles/text_models/gensim_bow/coherence_bow.csv')


num_topics  passes  perplexity  cv_coherence  umass_coherence
0           10     200   -6.998504      0.530079        -1.928838
1           10     200   -7.003896      0.527507        -1.899064
2           10     200   -7.009518      0.522806        -1.941300
3           10     250   -6.998219      0.527192        -1.926723
4           10     250   -7.003660      0.527507        -1.899524
5           10     250   -7.009314      0.521979        -1.939337
6           10     300   -6.998064      0.527192        -1.925657
7           10     300   -7.003501      0.527507        -1.899750
8           10     300   -7.009193      0.521979        -1.939096
9           15     200   -6.927175      0.598702        -2.078357
10          15     200   -6.933657      0.550770        -2.347129
11          15     200   -6.937755      0.552097        -2.337840
12          15     250   -6.926745      0.601829        -2.033160
13          15     250   -6.933287      0.550770        -2.348002
14          15     250   -6.937144      0.547959        -2.323458
15          15     300   -6.926489      0.602920        -2.027883
16          15     300   -6.933044      0.550840        -2.346599
17          15     300   -6.936722      0.551394        -2.332016
18          20     200   -6.901848      0.563084        -2.608615
19          20     200   -6.906064      0.565873        -2.440997
20          20     200   -6.911796      0.566614        -2.494248
21          20     250   -6.901616      0.562748        -2.605916
22          20     250   -6.905698      0.565802        -2.478855
23          20     250   -6.911473      0.566744        -2.501407
24          20     300   -6.901448      0.562748        -2.605488
25          20     300   -6.905514      0.568321        -2.495676
26          20     300   -6.911339      0.566014        -2.502504
27          25     200   -6.876040      0.584290        -2.197082
28          25     200   -6.881162      0.586874        -2.256091
29          25     200   -6.884038      0.578831        -2.203432
30          25     250   -6.875610      0.584230        -2.193264
31          25     250   -6.880527      0.585364        -2.261674
32          25     250   -6.883790      0.578831        -2.202731
33          25     300   -6.875310      0.583049        -2.195336
34          25     300   -6.880278      0.585579        -2.259617
35          25     300   -6.883603      0.578043        -2.203229

In [12]:
## lets try and plot the coherence values
fig = px.bar(coherence_bow_df, y=['cv_coherence', 'umass_coherence'], title="Coherence Scores for different number of topics")
fig.show()

d:\workspace\Aletheia\env\lib\site-packages\plotly\io\_renderers.py:395: DeprecationWarning:

distutils Version classes are deprecated. Use packaging.version instead.

d:\workspace\Aletheia\env\lib\site-packages\plotly\io\_renderers.py:395: DeprecationWarning:

distutils Version classes are deprecated. Use packaging.version instead.



##### Notes
* From the above chart it looks like max we could attain is `0.602920` which is not ideal but also not too bad, looks like the model at index `15` is our best model. 


### Best Params

In [14]:
print(f"Ideal Params are: {coherence_bow_df.loc[coherence_bow_df['cv_coherence'].idxmax(),['num_topics', 'passes', ]]}")

Ideal Params are: num_topics     15.0
passes        300.0
Name: 15, dtype: float64


### Sanity Testing

In [ ]:
## Lets load the mode from pickle file and run some sanity tests. 
with open("../pickles/text_models/gensim_bow/15_topics_300_passes_100_iterations.pkl", 'rb') as model:
        lda = pickle.load(model)
        



In [81]:
random_text = data["clean_text"][102]
random_text

'supreme court chief justice john roberts granted a stay temporarily blocking former president trump from having to turn over his tax records to democrats on the house ways and means committee trump and his legal team on monday filed asking the supreme court to block the release of his tax records  the house ways and means committee first requested six years of trumps tax returns in  donald trumps request to keep tax returns from congress denied by appeals court upon consideration of the application of counsel for the applicants it is so ordered that the mandate of the united states court of appeals for the district of columbia circuit case no  is hereby stayed pending further order of the undersigned or of the court roberts’ order states requesting that the committee respond before thursday nov  by noon in  the justice department said congress should be able to review the records a decision trump and his legal team have appealed  us district judge trevor mcfadden ruled last december t

In [82]:
data_words = list(common_utils.sent_to_words([random_text]))

data_lemmatized = common_utils.tokenization(data_words)


100%|██████████| 1/1 [00:00<00:00, 26.25it/s]


In [83]:
bow = lda.id2word.doc2bow(data_lemmatized[0])

document_topics = lda.get_document_topics(bow)

In [84]:
sorted_document_topics = sorted(document_topics, key = lambda x: x[1], reverse=True)

for doc_topic in sorted_document_topics:
    print(f"Topic: {doc_topic[0]} - Probability: {doc_topic[1]}")


Topic: 11 - Probability: 0.6454530358314514
Topic: 2 - Probability: 0.20740783214569092
Topic: 12 - Probability: 0.0828285962343216
Topic: 9 - Probability: 0.05335969477891922


In [61]:
## lets try and get the top 10 words for each topic
top_words = lda.show_topics(formatted=False, num_words=10)

In [85]:
lda.show_topic(11)

[('fbi', 0.05228108),
 ('trump', 0.049099073),
 ('documents', 0.027911378),
 ('raid', 0.025399191),
 ('records', 0.023785453),
 ('investigation', 0.023728805),
 ('president', 0.022728289),
 ('doj', 0.018155092),
 ('maralago', 0.014479115),
 ('search', 0.014084321)]

## Gensim LDA with Bigram BOW

### Lemmatization

In [204]:
## lemmatization with bigrams
data_words_bigrams = common_utils.make_bigrams(data_words, bigram_mod)

data_lemmatized = common_utils.tokenization(data_words_bigrams)
# data_lemmatized = lemmatization_noun_chunks(data_words_bigrams)

# Remove Stop Words
## we are removing stop words in the lemmatization function using spacy is_stop flag
# data_words_nostops = remove_stopwords(data_lemmatized)

print(data_lemmatized[:1])

100%|██████████| 3972/3972 [03:45<00:00, 17.64it/s]

[['governor', 'term', 'sen_maggie_hassan', 'challenger', 'inflation', 'abortion', 'border', 'crisis', 'denialism', 'debate', 'race', 'gop', 'senate', 'majority', 'crossfire', 'debate', 'army', 'tours', 'duty', 'war', 'afghanistan', 'debate', 'saint_anselm_college_new_hampshire_institute', 'wednesday_evening', 'bolduc', 'campaign', 'bystander', 'crowd', 'debate', 'swing', 'campaign', 'bolduc', 'rick_wiley', 'bolduc', 'campaign', 'fox_news', 'punch', 'activist', 'stake', 'midterm_elections', 'hassans', 'campaign', 'communications_director', 'kevin_donohoe', 'incident', 'behavior', 'activist', 'campaign', 'volunteers', 'debate', 'bolduc', 'altercation', 'debate', 'hassan', 'attack', 'speaker_nancy', 'pelosi', 'husband', 'san_francisco', 'gop', 'senate', 'nominee', 'problems', 'republicans', 'democrat', 'fuel', 'individual', 'bolduc', 'campaign', 'spokesperson', 'kate_constantini', 'fox_news', 'tonight', 'temperature', 'discourse', 'debate', 'individual', 'crowd', 'gathered_outside', 'resp

### Create Dictionary & Corpus

In [205]:
# Create Dictionary
id2word = corpora.Dictionary(data_lemmatized)
# id2word.filter_extremes(no_below=10, no_above=0.75, keep_n=10000)


# Create Corpus
texts = data_lemmatized

# Term Document Frequency
corpus = [id2word.doc2bow(text) for text in texts]

# View
print(corpus[:1])

[[(0, 7), (1, 2), (2, 1), (3, 1), (4, 1), (5, 2), (6, 1), (7, 1), (8, 1), (9, 2), (10, 1), (11, 1), (12, 1), (13, 1), (14, 1), (15, 1), (16, 1), (17, 1), (18, 13), (19, 1), (20, 1), (21, 1), (22, 1), (23, 9), (24, 1), (25, 2), (26, 1), (27, 1), (28, 1), (29, 1), (30, 1), (31, 1), (32, 1), (33, 1), (34, 1), (35, 1), (36, 1), (37, 2), (38, 1), (39, 11), (40, 2), (41, 1), (42, 1), (43, 1), (44, 1), (45, 2), (46, 1), (47, 1), (48, 1), (49, 1), (50, 1), (51, 1), (52, 1), (53, 1), (54, 1), (55, 1), (56, 1), (57, 1), (58, 1), (59, 2), (60, 4), (61, 1), (62, 1), (63, 1), (64, 1), (65, 1), (66, 1), (67, 7), (68, 1), (69, 1), (70, 5), (71, 1), (72, 8), (73, 1), (74, 1), (75, 1), (76, 1), (77, 1), (78, 1), (79, 2), (80, 3), (81, 1), (82, 1), (83, 1), (84, 1), (85, 1), (86, 1), (87, 1), (88, 1), (89, 2), (90, 1), (91, 1), (92, 1), (93, 2), (94, 1), (95, 1), (96, 1), (97, 1), (98, 1), (99, 1), (100, 3), (101, 1), (102, 4), (103, 3), (104, 3), (105, 1), (106, 2), (107, 1), (108, 1), (109, 1), (110, 

In [206]:
# Human readable format of corpus (term-frequency)
[[(id2word[id], freq) for id, freq in cp] for cp in corpus[:1]]


[[('abortion', 7),
  ('activist', 2),
  ('afghanistan', 1),
  ('altercation', 1),
  ('app', 1),
  ('army', 2),
  ('attack', 1),
  ('attacks', 1),
  ('ballot', 1),
  ('ban', 2),
  ('behavior', 1),
  ('bid', 1),
  ('biden', 1),
  ('biden_administration', 1),
  ('big_lie', 1),
  ('big_pharma', 1),
  ('bills', 1),
  ('blockbuster_move', 1),
  ('bolduc', 13),
  ('border', 1),
  ('bottom_line', 1),
  ('buldoc', 1),
  ('bystander', 1),
  ('campaign', 9),
  ('candidates', 1),
  ('challenger', 2),
  ('chance', 1),
  ('chuck_morse', 1),
  ('click_here', 1),
  ('clips', 1),
  ('combustible_issue', 1),
  ('communications_director', 1),
  ('conclusion', 1),
  ('contest', 1),
  ('credentials', 1),
  ('crisis', 1),
  ('crossfire', 1),
  ('crowd', 2),
  ('cycle', 1),
  ('debate', 11),
  ('decisions', 2),
  ('democrat', 1),
  ('denialism', 1),
  ('discourse', 1),
  ('doctor', 1),
  ('don_bolduc', 2),
  ('donald_trump_repeated_unproven', 1),
  ('dumps', 1),
  ('duty', 1),
  ('earlier_this_month', 1),
  

### Building the Topic Model

In [153]:
# lda_model = LdaModel(corpus=corpus,
#                      id2word=id2word,
#                      num_topics=20,
#                      random_state=100,
#                      update_every=1,
#                     #  chunksize=200,
#                      passes=250,
#                      alpha='auto',
#                      per_word_topics=True)

lda_model = LdaModel(corpus=corpus,
                     id2word=id2word,
                     num_topics=20,
                     random_state=100,
                     update_every=1,
                    #  chunksize=200,
                     passes=250,
                     alpha='auto',
                     per_word_topics=True)


In [154]:
# Print the Keyword in the 10 topics
pprint(lda_model.print_topics())
# doc_lda = lda_model[corpus]

[(0,
  '0.082*"trump" + 0.041*"president" + 0.033*"committee" + 0.017*"capitol" + '
  '0.012*"cheney" + 0.012*"fox" + 0.010*"donald_trump" + 0.009*"app" + '
  '0.009*"congress" + 0.008*"rep"'),
 (1,
  '0.018*"hunter" + 0.017*"hunter_biden" + 0.014*"letter" + 0.013*"biden" + '
  '0.013*"investigation" + 0.012*"fox" + 0.009*"president" + 0.008*"fox_news" '
  '+ 0.007*"emails" + 0.006*"johnson"'),
 (2,
  '0.038*"arizona" + 0.020*"alaska" + 0.017*"lake" + 0.016*"hobbs" + '
  '0.010*"kari_lake" + 0.008*"bush" + 0.008*"katie_hobbs" + 0.008*"murkowski" '
  '+ 0.007*"slavery" + 0.006*"constitution"'),
 (3,
  '0.025*"voters" + 0.021*"democrats" + 0.019*"gop" + 0.019*"senate" + '
  '0.018*"race" + 0.017*"campaign" + 0.016*"candidates" + 0.015*"fox" + '
  '0.015*"republicans" + 0.014*"candidate"'),
 (4,
  '0.035*"desantis" + 0.035*"florida" + 0.022*"governor" + 0.019*"president" + '
  '0.012*"fox" + 0.012*"fox_news" + 0.009*"california" + 0.008*"gop" + '
  '0.008*"iowa" + 0.008*"app"'),
 (5,
  '0

##### Notes
* So visually it seems we have a different topics when we use `bigrams`. 

### Analyzing Model

In [157]:
# Compute Perplexity
print('\nPerplexity: ', lda_model.log_perplexity(corpus))  # a measure of how good the model is. lower the better.

# Compute Coherence Score
coherence_model_lda = CoherenceModel(model=lda_model, texts=data_lemmatized, corpus=corpus, dictionary=id2word, coherence='u_mass')
coherence_lda = coherence_model_lda.get_coherence()
print('\nCoherence Score: ', coherence_lda)


Perplexity:  -8.758935949671814

Coherence Score:  -3.140279325133822


Promising Models
```
lda_model = LdaModel(corpus=corpus,
                     id2word=id2word,
                     num_topics=20,
                     random_state=100,
                     update_every=1,
                    #  chunksize=200,
                     passes=250,
                     alpha='auto',
                     per_word_topics=True)


Perplexity:  -8.535495028799938
Coherence Score:  0.4446532328940426
```
--------------------------------------------------------




### Visualize Topics

In [158]:
# Visualize the topics
pyLDAvis.enable_notebook()
vis = gensimvis.prepare(lda_model, corpus, id2word)
vis

d:\workspace\Aletheia\env\lib\site-packages\pyLDAvis\_prepare.py:247: FutureWarning:

In a future version of pandas all arguments of DataFrame.drop except for the argument 'labels' will be keyword-only.



PreparedData(topic_coordinates=              x         y  topics  cluster       Freq
topic                                                
3     -0.175245  0.228185       1        1  16.950449
17    -0.182541  0.097560       2        1   9.714046
15    -0.088264 -0.112788       3        1   7.658048
13    -0.038216 -0.026436       4        1   7.604836
7     -0.131244 -0.057232       5        1   6.376240
18    -0.040290 -0.008012       6        1   6.275188
12    -0.128878 -0.068422       7        1   5.618938
16     0.028273 -0.135427       8        1   5.377310
10    -0.011098  0.029322       9        1   5.227934
4     -0.095437  0.092261      10        1   4.938332
0     -0.059230 -0.021056      11        1   4.741323
8     -0.066580 -0.149656      12        1   4.349092
6     -0.019344 -0.123060      13        1   3.641226
9      0.024911  0.232339      14        1   2.717654
1      0.059898 -0.047418      15        1   2.594392
19     0.106913 -0.102055      16        1   1.903250
5      0.149384  0.000773      17        1   1.605950
14     0.208074  0.055628      18        1   0.951428
2      0.221938  0.103010      19        1   0.895598
11     0.236975  0.012484      20        1   0.858767, topic_info=           Term         Freq        Total Category  logprob  loglift
157       trump  4414.000000  4414.000000  Default  30.0000  30.0000
0      abortion  3324.000000  3324.000000  Default  29.0000  29.0000
12        biden  5913.000000  5913.000000  Default  28.0000  28.0000
114   president  7866.000000  7866.000000  Default  27.0000  27.0000
183   democrats  5320.000000  5320.000000  Default  26.0000  26.0000
...         ...          ...          ...      ...      ...      ...
606      russia    33.638043   546.497124  Topic20  -4.9619   1.9696
2265    charges    28.192692   307.647884  Topic20  -5.1385   2.3675
157       trump    47.810029  4414.190911  Topic20  -4.6103   0.2321
312     witness    20.744613    81.735485  Topic20  -5.4453   3.3862
1681      agent    20.504518   180.447338  Topic20  -5.4569   2.5826

[1315 rows x 6 columns], token_table=       Topic      Freq          Term
term                                
678        3  0.994246        abbott
678       10  0.003127        abbott
20281      2  0.963079           abe
2013       4  0.981212  abolitionist
0          1  0.180172      abortion
...      ...       ...           ...
5789      14  0.944919     youngkins
2641       9  0.992493        zeldin
263        9  0.982873       zeldins
25281     15  0.915701         zhang
9918      15  0.902524    zuckerberg

[3442 rows x 3 columns], R=30, lambda_step=0.01, plot_opts={'xlab': 'PC1', 'ylab': 'PC2'}, topic_order=[4, 18, 16, 14, 8, 19, 13, 17, 11, 5, 1, 9, 7, 10, 2, 20, 6, 15, 3, 12])

### Finding Best Params

In [207]:
## compute_coherence_values(corpus, id2word, texts, num_topics, passes, chunk_sizes=[200], iterations=[100]):
model_list, coherence_values, params = gensim_utils.compute_coherence_values(corpus=corpus, id2word=id2word, texts=data_lemmatized, num_topics=[10, 15, 20, 25], passes=[200, 250, 300], iterations=[100, 120, 150])

  0%|          | 0/4 [00:00<?, ?it/s]



100%|██████████| 3/3 [24:23<00:00, 487.88s/it]




100%|██████████| 3/3 [29:39<00:00, 593.26s/it]




 25%|██▌       | 1/4 [1:29:14<4:27:42, 5354.31s/it]



100%|██████████| 3/3 [24:36<00:00, 492.30s/it]




100%|██████████| 3/3 [30:22<00:00, 607.35s/it]




 50%|█████     | 2/4 [3:00:28<3:00:50, 5425.02s/it]



100%|██████████| 3/3 [26:19<00:00, 526.47s/it]




100%|██████████| 3/3 [33:19<00:00, 666.47s/it]




 75%|███████▌  | 3/4 [4:38:47<1:34:01, 5641.27s/it]



100%|██████████| 3/3 [27:44<00:00, 554.71s/it]




100%|██████████| 3/3 [33:45<00:00, 675.07s/it]




100%|██████████| 4/4 [6:19:59<00:00, 5699.91s/it]  


In [211]:
## lets write to pickle file for future use
## commenting this code to prevent overwriting the files
# for models in model_list:
#     with open(f"../pickles/text_models/gensim_bigram/{models.num_topics}_topics_{models.passes}_passes_{models.iterations}_iterations.pkl", "wb") as f:
#         pickle.dump(models, f)
# ## les convert the coherence_values list to a dataframe

# coherence_values_df = pd.DataFrame(coherence_values, columns=['perplexity', 'cv_coherence', 'umass_coherence'])


# params_df = pd.DataFrame(params, columns=['num_topics', 'passes', 'iterations'])


# combined_df = pd.concat([params_df, coherence_values_df], axis=1)
# combined_df

# combined_df.to_csv('../pickles/text_models/gensim_bigram/combined_df.csv', index=False)

### Plotting GridSearch Results

In [7]:
coherence_values_df = pd.read_csv('../pickles/text_models/gensim_bigram/combined_df.csv')
coherence_values_df

num_topics  passes  iterations  perplexity  cv_coherence  umass_coherence
0           10     200         100   -8.270029      0.472249        -2.186222
1           10     200         120   -8.273810      0.459705        -2.194383
2           10     200         150   -8.278741      0.454264        -2.287050
3           10     250         100   -8.268745      0.470480        -2.176113
4           10     250         120   -8.272758      0.467805        -2.180342
5           10     250         150   -8.277754      0.454264        -2.283637
6           10     300         100   -8.267961      0.470480        -2.178966
7           10     300         120   -8.271850      0.467805        -2.181999
8           10     300         150   -8.277023      0.454264        -2.283470
9           15     200         100   -8.598768      0.500653        -3.692057
10          15     200         120   -8.603043      0.511913        -3.848273
11          15     200         150   -8.605266      0.513645        -3.690479
12          15     250         100   -8.598460      0.500227        -3.682967
13          15     250         120   -8.602740      0.513583        -3.810153
14          15     250         150   -8.605007      0.515741        -3.727415
15          15     300         100   -8.598263      0.500227        -3.684848
16          15     300         120   -8.602550      0.513583        -3.810334
17          15     300         150   -8.604766      0.515741        -3.727474
18          20     200         100   -8.762567      0.525921        -3.195866
19          20     200         120   -8.766648      0.521401        -3.269142
20          20     200         150   -8.771130      0.526862        -3.238188
21          20     250         100   -8.762318      0.525921        -3.192209
22          20     250         120   -8.766379      0.521401        -3.270467
23          20     250         150   -8.770788      0.526862        -3.237604
24          20     300         100   -8.762142      0.521172        -3.113222
25          20     300         120   -8.766197      0.521401        -3.270192
26          20     300         150   -8.770569      0.526862        -3.239096
27          25     200         100   -8.944709      0.527496        -3.425895
28          25     200         120   -8.946258      0.522622        -3.499643
29          25     200         150   -8.949378      0.533622        -3.378826
30          25     250         100   -8.944313      0.526254        -3.436446
31          25     250         120   -8.946027      0.524075        -3.465595
32          25     250         150   -8.948971      0.534290        -3.411002
33          25     300         100   -8.944047      0.527440        -3.432244
34          25     300         120   -8.945705      0.524284        -3.474803
35          25     300         150   -8.948610      0.535385        -3.432476